In [1]:
import pandas as pd
import numpy as np
import sys
import os
import folium
import folium.plugins
from IPython.display import HTML, display
import geojson

In [16]:
# Create an empty map

# OStamen Terrain
m = folium.Map(location=[40.767937,-73.982155 ], tiles="Stamen Toner", zoom_start=12)



# Get Greenthumb data
green_data = pd.read_csv('NYC_Greenthumb_Community_Gardens.csv')
green_data = green_data[['Latitude','Longitude','Garden Name','Size','Boro']].copy()
green_data = green_data.loc[green_data['Boro'] == 'M']
green_data = green_data[pd.notnull(green_data['Latitude'])]

for index, row in green_data.iterrows():
    folium.RegularPolygonMarker([row['Latitude'],row['Longitude']],
                    radius= 2,
                    color = '#3cb371',
                    number_of_sides=3,
                    fill_color='#3cb371',
                   ).add_to(m)

m

In [3]:
condo = pd.read_csv('DOF__Condominium_comparable_rental_income___Manhattan_-_FY_2010_2011.csv')

In [4]:
condo_est = condo[['Latitude','Longitude','NTA','MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt',
                  'MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt']]

# Check the distribution of overal performance
rent_est = pd.DataFrame({'Rent': condo_est['MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt']})
print (rent_est.describe())
value_est = pd.DataFrame({'Value': condo_est['MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt']})
print (value_est.describe())

              Rent
count  1165.000000
mean     35.011665
std       8.109061
min       0.000000
25%      30.000000
50%      35.000000
75%      40.200000
max      67.000000
             Value
count  1165.000000
mean    164.017339
std      45.984265
min      28.500000
25%     139.000000
50%     163.000000
75%     197.000000
max     311.000000


In [5]:
# Plot est. value on map
condo_est = condo_est[pd.notnull(condo_est['Latitude'])]

m2 = folium.Map(location=[40.767937,-73.982155 ], tiles="Stamen Toner", zoom_start=12)


condo_est['Condo_c'] = np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt'] <= 30, '#fef0d9', 
                                 np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt'] <= 35, '#fdcc8a', 
                                          np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt'] <=40,'#d7301f','#d7301f' )))

# add color to different rent


for index, row in condo_est.iterrows():
    folium.CircleMarker([row['Latitude'],row['Longitude']],
                        radius= 1,
                        color = row['Condo_c'],
                        fill = True,
                        fill_color= row['Condo_c'],
                       ).add_to(m2)
m2

In [6]:
m3 = folium.Map(location=[40.767937,-73.982155 ], tiles="Stamen Toner", zoom_start=12)

condo_est['Condo_v'] = np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt'] <= 139, '#fef0d9', 
                                 np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt'] <= 163, '#fdcc8a', 
                                          np.where(condo_est['MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt'] <=197,'#d7301f','#d7301f' )))
for index, row in condo_est.iterrows():
    folium.CircleMarker([row['Latitude'],row['Longitude']],
                        radius= 1,
                        color = row['Condo_v'],
                        fill = True,
                        fill_color= row['Condo_v'],
                       ).add_to(m3)
m3

In [7]:
m4 = folium.Map(location=[40.767937,-73.982155 ], tiles="Stamen Toner", zoom_start=12)

for index, row in condo_est.iterrows():
    folium.CircleMarker([row['Latitude'],row['Longitude']],
                        radius= 1,
                        color = row['Condo_v'],
                        fill = True,
                        fill_color= row['Condo_v'],
                       ).add_to(m4)

for index, row in green_data.iterrows():
    folium.RegularPolygonMarker([row['Latitude'],row['Longitude']],
                    radius= 3,
                    color = '#2E8B57',
                    number_of_sides=3,
                    fill_color='#2E8B57',
                   ).add_to(m4)
m4 # House Value Plot plus greenthumb

In [8]:
# Calcualte median price for each nta
condo_median = condo[['NTA','MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt',
                  'MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt']]

condo_rent_median = condo_median.groupby(['NTA'])['MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt'].median()
condo_value_median = condo_median.groupby(['NTA'])['MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt'].median()

condo_rent_median = pd.DataFrame(condo_rent_median)
condo_value_median= pd.DataFrame(condo_value_median)


In [10]:
neighborhoods = os.path.join('nta_m.json')
 
rent = os.path.join('medianrent.csv')
rent = pd.read_csv(rent)

m5 = folium.Map(location=[40.767937,-73.982155 ],  zoom_start=12)
# Add the color for the chloropleth:
m5.choropleth(
    geo_data= neighborhoods,
    name='choropleth',
    data=rent,
    columns=['ID', 'MANHATTAN CONDOMINIUM PROPERTY Gross Income per SqFt'],
    key_on='feature.id',
    fill_color='OrRd',
    fill_opacity=0.9,
    line_opacity=0.2,
    legend_name='Rent Price per sqft',
)
folium.LayerControl().add_to(m5)
 
# Save to html
m5

In [11]:
# Add greenthumb
for index, row in green_data.iterrows():
    folium.RegularPolygonMarker([row['Latitude'],row['Longitude']],
                    radius= 2,
                    color = '#3cb371',
                    number_of_sides=3,
                    fill_color='#3cb371',
                   ).add_to(m5)
m5

In [12]:
neighborhoods = os.path.join('nta_m.json')
 
value = os.path.join('valuemedian.csv')
value = pd.read_csv(value)

m6 = folium.Map(location=[40.767937,-73.982155 ], zoom_start=12)
# Add the color for the chloropleth:
m6.choropleth(
    geo_data= neighborhoods,
    name='choropleth',
    data=value,
    columns=['ID', 'MANHATTAN CONDOMINIUM PROPERTY Market Value per SqFt'],
    key_on='feature.id',
    fill_color='OrRd',
    fill_opacity=0.9,
    line_opacity=0.2,
    legend_name='Market Value per sqft',
)
folium.LayerControl().add_to(m6)
 
# Save to html
m6

In [13]:
# Add greenthumb
for index, row in green_data.iterrows():
    folium.RegularPolygonMarker([row['Latitude'],row['Longitude']],
                    radius= 2,
                    color = '#3cb371',
                    number_of_sides=3,
                    fill_color='#3cb371',
                   ).add_to(m6)
m6

In [14]:
# Property number
condo_number = condo_median['NTA'].value_counts()
condo_number = pd.read_csv('counts.csv')
m7 = folium.Map(location=[40.767937,-73.982155 ], zoom_start=12)
# Add the color for the chloropleth:
m7.choropleth(
    geo_data= neighborhoods,
    name='choropleth',
    data=condo_number ,
    columns=['ID', 'COUNTS'],
    key_on='feature.id',
    fill_color='OrRd',
    fill_opacity=0.9,
    line_opacity=0.2,
    legend_name='Number of Properties',
)
folium.LayerControl().add_to(m7)

m7